In [105]:
import os
import xarray as xr
import numpy as np
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
from tqdm import tqdm

# Set global variables
PROJECT = r"D:\World Bank\Paper - Child mortality and Climate Shocks"
OUTPUTS = rf"{PROJECT}\Outputs"
DATA = rf"{PROJECT}\Data"
DATA_IN = rf"{DATA}\Data_in"
DATA_PROC = rf"{DATA}\Data_proc"
DATA_OUT = rf"{DATA}\Data_out"
ERA5_DATA = rf"Z:\WB Data\ERA5 Reanalysis"

In [ ]:
import xarray as xr
xr.open_dataset(r"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\ERA5-Land_monthly_1970-2021.nc")

In [ ]:

era5_path = r"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\ERA5-Land_monthly_1970-2021.nc"
precipitation = xr.open_dataset(
    era5_path, 
    chunks={"time":1224, "lat": 400, "lon": 400}
)
# -64.916145,-25.110773,-40.124386,-4.511651
precipitation = precipitation.sel(lon=slice(-60, -50), lat=slice(-25, -15))
precipitation = precipitation.sel(time=precipitation["time.day"] == 1)

precipitation.to_netcdf(rf"{DATA_PROC}\ERA5-Land_monthly_1970-2021_subset.nc")

In [106]:
import os
import warnings
import xarray as xr
from tqdm import tqdm
from climate_indices import indices, compute
from dask.diagnostics import ProgressBar
# from dask.distributed import Client

era5_path = r"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\ERA5-Land_monthly_1970-2021.nc"
precipitation = xr.open_dataset(
    rf"{DATA_PROC}\ERA5-Land_monthly_1970-2021_subset.nc", 
    chunks={"time":-1, "lat": 400, "lon": 400}
)

i = 1
da_precip_groupby = precipitation["tp"].stack(point=("lat", "lon")).groupby(group="point")



In [107]:
import xarray as xr
from climate_indices import indices, compute

precipitation = xr.open_dataset(
    rf"{DATA_PROC}\ERA5_monthly_1970-2021.nc", 
    chunks={"time":-1, "lat": 400, "lon": 400}
)

precipitation = precipitation.sel(lon=slice(-60, -50), lat=slice(-25, -15))

# Filter between 1970 and 1990 to reduce size
precipitation = precipitation.sel(time=slice("1970", "1972"))

da_precip_groupby = precipitation["tp"].stack(point=("lat", "lon")).groupby(group="point")

distribution = indices.Distribution.gamma
data_start_year = 1970
calibration_year_initial = 1970
calibration_year_final = 1972
periodicity = compute.Periodicity.monthly

da_spi = xr.apply_ufunc(
    indices.spi,
    da_precip_groupby,
    i,
    distribution,
    data_start_year,
    calibration_year_initial,
    calibration_year_final,
    periodicity,
    dask="parallelized",
)
da_spi = da_spi.unstack("point").rename(f"spi{i}")

C:\Users\ofici\AppData\Roaming\Python\Python311\site-packages\climate_indices\compute.py:707: RuntimeWarning:

Mean of empty slice

C:\Users\ofici\AppData\Roaming\Python\Python311\site-packages\climate_indices\compute.py:710: RuntimeWarning:

Mean of empty slice

C:\Users\ofici\AppData\Roaming\Python\Python311\site-packages\climate_indices\compute.py:707: RuntimeWarning:

Mean of empty slice

C:\Users\ofici\AppData\Roaming\Python\Python311\site-packages\climate_indices\compute.py:710: RuntimeWarning:

Mean of empty slice

C:\Users\ofici\AppData\Roaming\Python\Python311\site-packages\climate_indices\compute.py:707: RuntimeWarning:

Mean of empty slice

C:\Users\ofici\AppData\Roaming\Python\Python311\site-packages\climate_indices\compute.py:710: RuntimeWarning:

Mean of empty slice

C:\Users\ofici\AppData\Roaming\Python\Python311\site-packages\climate_indices\compute.py:707: RuntimeWarning:

Mean of empty slice

C:\Users\ofici\AppData\Roaming\Python\Python311\site-packages\climate_indice

KeyboardInterrupt: 

In [13]:
da_spi.compute()

ValueError: Invalid periodicity argument: monthly

In [ ]:
# da_spi.isel(time=7).plot()

In [ ]:
!pip install climate_indices --upgrade 

In [ ]:
import climate_indices
climate_indices.indices.__version__

In [ ]:
da_spi

In [ ]:
precipitation = precipitation.load()
da_precip_groupby = precipitation["tp"].stack(point=("lat", "lon")).groupby(group="point")


In [ ]:
# Parameters
import numpy as np
import dask.array as da

distribution = indices.Distribution.gamma
data_start_year = 1970
calibration_year_initial = 1970
calibration_year_final = 1972
periodicity = compute.Periodicity.monthly

spi_path = f"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\ERA5-Land_monthly_1970-2021_SPI{i}.nc"

# Filter runtime warnings
warnings.filterwarnings("ignore", category=RuntimeWarning)
da_spi = xr.apply_ufunc(
    indices.spi,
    da_precip_groupby,
    i,
    distribution,
    data_start_year,
    calibration_year_initial,
    calibration_year_final,
    periodicity,
    dask="parallelized",
)
da_spi = da_spi.unstack("point").rename(f"spi{i}")
# with ProgressBar():
#     encoding = {
#         var: {"zlib": True, "complevel": 5} for var in [da_spi.name]
#     }
#     da_spi.to_netcdf(
#         spi_path,
#         encoding=encoding,
#     )   

In [ ]:
with ProgressBar():
    da_spi.to_netcdf(
        spi_path,
    )   
    

In [ ]:
da_spi.isel(time=50).plot()

In [ ]:
da_spi.to_netcdf(
    spi_path,
)   

In [ ]:
da_spi

In [ ]:
da_spi.mean(dim=["lat", "lon"]).isel(time=slice(0, 500)).plot()

In [ ]:
precipitation

In [ ]:
da_spi

In [ ]:
# Select Buenos Aires
precipitation = precipitation.sel(lat=slice(-35.5, -35), lon=slice(-58.5, -58))

In [ ]:
import pandas as pd
pd.set_option('display.max_columns', 500)
df = pd.read_parquet(r"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\births_climate_4500000.parquet")

In [ ]:
import xarray as xr

ds = xr.open_dataset(r"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\Climate_shocks_v4.nc")

In [ ]:
sub_ds.time.values.shape

In [ ]:
# Set global variables
PROJECT = r"D:\World Bank\Paper - Child Mortality and Climate Shocks"
OUTPUTS = rf"{PROJECT}\Outputs"
DATA = rf"{PROJECT}\Data"
DATA_IN = rf"{DATA}\Data_in"
DATA_PROC = rf"{DATA}\Data_proc"
DATA_OUT = rf"{DATA}\Data_out"

### Load data #############
full_dhs = pd.read_stata(rf"{DATA_IN}/DHS/DHSBirthsGlobalAnalysis_05142024.dta")
full_dhs["ID"] = full_dhs.index
df = full_dhs.copy()


In [ ]:
    def get_climate_shock(from_date, to_date, lat, lon):
        if pd.isna(from_date):
            return np.nan

        # Filter point
        # climate_data_vars = climate_data[climate_variables]
        point_data = ds.sel(time=slice(from_date, to_date)).sel(
            lat=lat, lon=lon
        )

        # Get position of original data
        lat = point_data.lat.item()
        lon = point_data.lon.item()

        # Filter by time
        inutero_to_1st_year = point_data.isel(time=slice(0, 22))
        out = compute_stats(inutero_to_1st_year)
        # Agregar columnas acá...
        return out


In [ ]:
def compute_stats(ds):
    
    arr = ds.to_array().values
    inutero = arr[:, :9]
    born_1m = arr[:,9:11]
    born_2to12m = arr[:,11:22]

    assert inutero.shape[1] == 9, inutero.shape[1] # 9 months in utero
    assert born_1m.shape[1] == 2, born_1m.shape[1] # 1 month after birth (a little bit more because we dont have climate data for the exact day of birth. On average is one month)
    assert born_2to12m.shape[1] == 11, born_2to12m.shape[1] # next 11 months after birth
    
    # Compute stats using numpy for efficiency
    inutero = {f"{var}_inutero_mean":value for var, value in zip(ds.data_vars, np.nanmean(inutero, axis=1))}
    born_1m = {f"{var}_born_1m_mean":value for var, value in zip(ds.data_vars, np.nanmean(born_1m, axis=1))}
    born_2to12m = {f"{var}_born_2to12m_mean":value for var, value in zip(ds.data_vars, np.nanmean(born_2to12m, axis=1))}

    results = {**inutero, **born_1m, **born_2to12m}
    results = pd.Series(results)
    return results

results = compute_stats(sub_ds)
results

In [ ]:
df["day"] = 1
df["month"] = df["chb_month"].astype(float)
df["year"] = df["chb_year"].astype(float)
df["birthdate"] = pd.to_datetime(df[["year", "month", "day"]]).to_numpy()

# Maximum range of dates
df["from_date"] = df["birthdate"] + pd.DateOffset(
    months=-9
)  # From in utero (9 months before birth)
df["to_date"] = df["birthdate"] + pd.DateOffset(
    months=13
)  # To the first year of life

# Filter children from_date greater than 1990 (we only have climate data from 1990)
df = df[df["from_date"] > "1990-01-01"]

# Filter children to_date smalle than 2021 (we only have climate data to 2020)
df = df[df["to_date"] < "2021-01-01"]

df["lat_round"] = (df["LATNUM"] * 4).round() / 4
df["lon_round"] = (df["LONGNUM"] * 4).round() / 4
df = df.reset_index(drop=True)



In [ ]:
from tqdm import tqdm  # for notebooks
tqdm.pandas()

climate_results = df.head(10_000).progress_apply(
    lambda s: get_climate_shock(
        s["from_date"],
        s["to_date"],
        s["lat_round"],
        s["lon_round"],
    ),
    axis=1,
)


In [ ]:
df[df.ID == 231181]

In [ ]:
s["from_date"].item()

In [ ]:
climate_results = df[df.ID == 231181].progress_apply(
    lambda s: get_climate_shock(
        s["from_date"],
        s["to_date"],
        s["lat_round"],
        s["lon_round"],
    ),
    axis=1,
)
climate_results

In [ ]:
df[df.ID == 231181]

In [ ]:
pd.read_parquet(r"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\births_climate_200000.parquet")

In [ ]:
s = df.head(1)

ds.sel(lat=41.75, lon=19.75, time=slice(s["from_date"].item(), s["to_date"].item())).mean()

In [ ]:
get_climate_shock(
    s["from_date"].item(),
    s["to_date"].item(),
    s["lat_round"].item(),
    s["lon_round"].item(),
)


In [ ]:
import os
import re
import shutil

folders = os.listdir(r"D:\Datasets\ERA5 Reanalysis\monthly-land")
folders = [f for f in folders if "." not in f]

for folder in folders:
    name = folder
    print(name)
    data_file = os.listdir(rf"D:\Datasets\ERA5 Reanalysis\monthly-land\{folder}")
    source_file = rf"D:\Datasets\ERA5 Reanalysis\monthly-land\{folder}\{data_file[0]}"
    destination_file = rf"D:\Datasets\ERA5 Reanalysis\monthly-land\{name}.nc"
    
    # Copy file to monthly-land folder
    shutil.copy2(source_file, destination_file)

    
# to_names = [re.sub(r"\((\d+)\)", rf"{1970+\1}", f) for f in files] 
# to_names

In [ ]:
{f"{var}_inutero_mean":value for var, value in zip(sub_ds.data_vars, arr.mean(axis=1))}

In [ ]:
[d for d in sub_ds.data_vars]

In [ ]:
pd.DataFrame().from_dict(results)

In [ ]:
sub_ds.to_array().values.shape

In [ ]:
compute_stats(sub_ds.to_array().values)

In [ ]:
def compute_stats(data):
    return np.mean(data, axis=0), np.min(data, axis=0), np.max(data, axis=0)

results = xr.apply_ufunc(
    compute_stats,
    sub_ds,
    input_core_dims=[["time"]],
    output_core_dims=[[], [], []],
    vectorize=False,
    output_dtypes=[np.float32, np.float32, np.float32],
)

results[0].to_array().values
# np.concatenate([r.to_array() for r in result])

In [ ]:
inutero = results[0].to_array().to_dataframe(name="inutero")["inutero"]
inutero.index = [f"{i}_inutero" for i in inutero.index]
inutero
# b30d = results[1].to_array().to_dataframe(name="b30d")["b30d"]

In [ ]:
pd.read_parquet(r"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\births_climate_100000.parquet")

In [ ]:
result

In [ ]:
country_hurr = pd.read_stata(r"D:\World Bank\CLIENT v2\Data\Data_out\IPUMS_hurricanes_wide.dta")

In [ ]:
country_floods = pd.read_stata(r"D:\World Bank\CLIENT v2\Data\Data_out\IPUMS_floods_wide.dta")

In [ ]:
country_dr = pd.read_stata(r"D:\World Bank\CLIENT v2\Data\Data_out\IPUMS_drought_wide.dta")

In [ ]:
ids = gpd.read_feather("D:\World Bank\CLIENT v2\Data\Data_proc\IPUMS_country_IDs.feather")


In [ ]:
country_dr[country_dr.cntry_code.isna()]

In [ ]:
chunk = pd.read_parquet(r"D:\World Bank\CLIENT v2\Data\Data_proc\shocks_by_adm\IPUMS\IPUMS_drought_SPEI24_25sd_1985_14_zonal_stats.parquet")

In [ ]:
chunk[chunk.index == 9826]

In [ ]:
ids = gpd.read_feather("D:\World Bank\CLIENT v2\Data\Data_proc\IPUMS_country_IDs.feather")
ids

In [ ]:
country_floods[(country_floods.cntry_code==275)]

In [ ]:
country_floods[(country_floods.cntry_code==275) & (country_floods.geolevel1==275045)]

In [ ]:
df = pd.read_parquet(r"D:\World Bank\CLIENT v2\Data\Data_proc\shocks_by_adm\IPUMS\out_floods_ungrouped.parquet")
df[df.ID == 4295]

In [ ]:
ds = xr.open_dataset(r"D:\World Bank\CLIENT v2\Data\Data_proc\IPUMS_country_grid.nc")

# 33.411341,29.633207,36.807021,33.532308
ds.sel(y=slice(33.532308,29.633207), x=slice(35,36)).ID.plot()          

In [ ]:
country_floods[country_floods.year.isna()]

In [ ]:
ids[ids.geometry.intersects(ids[ids.ID == 10320].geometry.values[0])].explore()

In [ ]:
ids[ids.ID == 10320]

In [ ]:
ids[ids.ID == 10320].explore()

In [ ]:
import geopandas as gpd
import pandas as pd
df = pd.read_csv(r"D:\World Bank\CLIENT v2\Data\Data_out\IPUMS_hurricanes_long.csv")

In [ ]:
df[df.CNTRY_CODE == 275]

In [ ]:
import xarray as xr
ds = xr.open_dataset(r"D:\World Bank\CLIENT v2\Data\Data_proc\ERA5_yearly_1970-2021_SPI-SPEI.nc")

In [ ]:
ds

# 35.112151,31.692255,35.288665,31.892901
ds.sel(year=1990, x=slice(35, 36), y=slice(32, 31))["SPI-1"].plot()

In [ ]:
import folium

col = gpd.read_file(r"D:\World Bank\CLIENT v2\Data\Data_raw\IPUMS Fixed\geo1_co1964_2005.shp")
m = col.set_crs("epsg:4326").explore()

# gdf = gpd.read_file(r"C:\Users\ofici\Downloads\geo2_co1973_2005\geo2_co1973_2005\geo2_co1973_2005.shp")
# m = gdf.explore(m=m)
# add layer selection
folium.LayerControl().add_to(m)  # use folium to add layer control
m

In [ ]:
col

In [ ]:
import xarray as xr

ds = xr.open_dataset(r"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\ERA5_monthly_1970-2021.nc")

In [ ]:
precipitation.sel(lat=slice(-25, -20), lon=slice(-65, -60)).isel(time=30)["t2m"].plot()

In [ ]:
precipitation = xr.open_dataset(
    r"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\ERA5_monthly_1970-2021.nc", chunks={"lat":721//2+1, "lon":1440//2}
)
precipitation

In [ ]:
from climate_indices import indices, compute
import xarray as xr
import warnings
import os

# Disable runtime warnings
warnings.filterwarnings("ignore", category=RuntimeWarning)

precipitation = xr.open_dataset(
    r"D:\World Bank\Paper - Child Mortality and Climate Shocks\Data\Data_proc\ERA5_monthly_1970-2021.nc", chunks={"lat":1000, "lon":1000}
)

# Select Argentina
# precipitation = precipitation.sel(lat=slice(-25, -20), lon=slice(-65, -60))

########################
####   Compute SPI  ####
########################

### Running this takes... A lot. Aprox. 90m for each SPI, so ~7.5h for all SPIs.

## Script based on: https://github.com/monocongo/climate_indices/issues/326
## Original paper: https://www.droughtmanagement.info/literature/AMS_Relationship_Drought_Frequency_Duration_Time_Scales_1993.pdf
## User guide to SPI: https://digitalcommons.unl.edu/cgi/viewcontent.cgi?article=1208&context=droughtfacpub
#   It is recommended to use SPI-9 or SPI-12 to compute droughts.
#   "SPI values below -1.5 for these timescales (SPI-9) are usually a good indication that dryness is having a significant impact on
#    agriculture and may be affecting other sectors as well."
## More here: https://www.researchgate.net/profile/Sorin-Cheval/publication/264467702_Spatiotemporal_variability_of_the_meteorological_drought_in_Romania_using_the_Standardized_Precipitation_Index_SPI/links/5842d18a08ae2d21756372f8/Spatiotemporal-variability-of-the-meteorological-drought-in-Romania-using-the-Standardized-Precipitation-Index-SPI.pdf
## Ignore negative values, they are normal: https://confluence.ecmwf.int/display/UDOC/Why+are+there+sometimes+small+negative+precipitation+accumulations+-+ecCodes+GRIB+FAQ

print("Data Ready! Computing SPI. This will take at least a few hours...")

# Mask data
print(precipitation)
da_precip_groupby = precipitation["tp"].stack(point=("lat", "lon")).groupby("point")

# Parameters
distribution = indices.Distribution.gamma
data_start_year = 1970
calibration_year_initial = 1970
calibration_year_final = 2020
periodicity = compute.Periodicity.monthly

# apply SPI to each `point`
spis = []
for i in [1, 3, 6, 9, 12]:
    print(f"Computing SPI-{i}")
    da_spi = xr.apply_ufunc(
        indices.spi,
        da_precip_groupby,
        i,
        distribution,
        data_start_year,
        calibration_year_initial,
        calibration_year_final,
        periodicity,
        dask="parallelized",
    )
    da_spi = da_spi.unstack("point").rename(f"spi{i}")
    break



In [ ]:
da_spi

In [ ]:
import pandas as pd

df = pd.read_csv(r"D:\World Bank\CLIENT v2\Data\Data_out\WB_drought_long.csv")
df

In [ ]:
da_spi.to_netcdf("test.nc")

In [ ]:
da_precip_groupby

In [ ]:
da_spi = xr.apply_ufunc(
    indices.spi,
    da_precip_groupby,
    3,
    distribution,
    data_start_year,
    calibration_year_initial,
    calibration_year_final,
    periodicity,
    dask="allowed",
)


In [ ]:
da_spi

In [ ]:
df = df.dropna(subset=["v008", "chb_year", "chb_month"], how="any")

# Date of interview
df["year"] = 1900+(df["v008"]-1)//12
df["month"] = df["v008"]-12*(df["year"]-1900)
df["day"] = 1
df["interview_date"]  = pd.to_datetime(df[["year", "month", "day"]], dayfirst=False)
df["interview_month"] = df["month"]
df["interview_day"]   = df["day"]
df = df.drop(columns=["year", "month", "day"])

# Date of birth
df["year"] = df["chb_year"].astype(int)
df["month"] = df["chb_month"].astype(int)
df["day"] = 15
df["birth_date"]  = pd.to_datetime(df[["year", "month", "day"]], dayfirst=False)
df = df.drop(columns=["year", "month", "day"])

# Number of days from interview
df["days_from_interview"] = df["interview_date"] - df["birth_date"]

# excluir del análisis a aquellos niños que nacieron 12 meses alrededor de la fecha de la encuesta y no más allá de 10 y 15 años del momento de la encuesta. 
# PREGUNTA PARA PAULA: ¿ella ya hizo el filtro de 15 años y 30 dias?
df["last_15_years"] = (df["days_from_interview"] > np.timedelta64(30, 'D')) & (df["days_from_interview"] < np.timedelta64(15*365, 'D'))
df["last_10_years"] = (df["days_from_interview"] > np.timedelta64(30, 'D')) & (df["days_from_interview"] < np.timedelta64(10*365, 'D'))
df["since_2003"] = (df["interview_year"]>=2003)
df = df[df["last_15_years"] == True]

In [ ]:
df["interview_year"]

In [ ]:
df

In [ ]:
df[["year", "month", "day"]]

In [ ]:
gen interview_year = v007
gen interview_month = v008-12*(interview_year-1900)

In [ ]:
files = os.listdir(ERA5_DATA)
datasets = []
for file in tqdm(files):
    ds = xr.open_dataset(os.path.join(ERA5_DATA, file))
    datasets += [ds]
precipitation = xr.concat(datasets, dim="time")
# precipitation.to_netcdf(os.path.join(DATA_OUT, "ERA5_monthly_1970-2021.nc"))

In [ ]:
xr.open_dataset(r"Z:\Laboral\World Bank\Paper - Child mortality and Climate Shocks\Data\Data_out\Climate_shocks_v3_spi.nc")

In [ ]:
import xarray as xr

climate_data = xr.open_dataset(r"Z:\Laboral\World Bank\Paper - Child mortality and Climate Shocks\Data\Data_out\Climate_shocks_v3_spi.nc")
climate_data

In [ ]:
def get_climate_shock(from_date, to_date, lat, lon):
    if pd.isna(from_date):
        return np.nan

    # Filter point
    point_data = climate_data.isel(time=slice(from_date, to_date)).sel(
        lat=lat, lon=lon, method="nearest"
    )

    # Get position of original data
    lat = point_data.lat.item()
    lon = point_data.lon.item()

    # Filter by time
    inutero_q1 = point_data.isel(time=slice(0, 3))
    inutero_q2 = point_data.isel(time=slice(3, 6))
    inutero_q3 = point_data.isel(time=slice(6, 9))
    born_1m = point_data.isel(time=slice(9, 10))
    born_2to3m = point_data.isel(time=slice(10, 12))
    born_3to6m = point_data.isel(time=slice(12, 15))
    born_6to12m = point_data.isel(time=slice(15, 21))

    out_vars = [
        lat,
        lon,
    ]
    for spi in [
        "spi1",
        "spi3",
        "spi6",
        "spi9",
        "spi12",
    ]:
        # Compute mean values for SPI
        inutero_q1_mean = inutero_q1[spi].mean().item()
        inutero_q2_mean = inutero_q2[spi].mean().item()
        inutero_q3_mean = inutero_q3[spi].mean().item()
        born_1m_mean = born_1m[spi].mean().item()
        born_2to3m_mean = born_2to3m[spi].mean().item()
        born_3to6m_mean = born_3to6m[spi].mean().item()
        born_6to12m_mean = born_6to12m[spi].mean().item()

        out_vars_this_spi = [
            inutero_q1_mean,
            inutero_q2_mean,
            inutero_q3_mean,
            born_1m_mean,
            born_2to3m_mean,
            born_3to6m_mean,
            born_6to12m_mean,
        ]
        out_vars += out_vars_this_spi

    # Compute mean values for temperature
    inutero_q1_temp_mean = inutero_q1["t2m"].mean().item()
    inutero_q2_temp_mean = inutero_q2["t2m"].mean().item()
    inutero_q3_temp_mean = inutero_q3["t2m"].mean().item()
    born_1m_temp_mean = born_1m["t2m"].mean().item()
    born_2to3m_temp_mean = born_2to3m["t2m"].mean().item()
    born_3to6m_temp_mean = born_3to6m["t2m"].mean().item()
    born_6to12m_temp_mean = born_6to12m["t2m"].mean().item()

    out_vars_temp = [
        inutero_q1_temp_mean,
        inutero_q2_temp_mean,
        inutero_q3_temp_mean,
        born_1m_temp_mean,
        born_2to3m_temp_mean,
        born_3to6m_temp_mean,
        born_6to12m_temp_mean,
    ]
    out_vars += out_vars_temp

    return out_vars


In [ ]:
def get_climate_shock2(from_date, to_date, lat, lon):
    if pd.isna(from_date):
        return np.nan

    # Filter point
    point_data = climate_data.isel(time=slice(from_date, to_date)).sel(
        lat=lat, lon=lon, method="nearest"
    )

    # Get position of original data
    lat = point_data.lat.item()
    lon = point_data.lon.item()

    # Filter by time
    inutero_q1 = point_data.isel(time=slice(0, 3))
    inutero_q2 = point_data.isel(time=slice(3, 6))
    inutero_q3 = point_data.isel(time=slice(6, 9))
    born_1m = point_data.isel(time=slice(9, 10))
    born_2to3m = point_data.isel(time=slice(10, 12))
    born_3to6m = point_data.isel(time=slice(12, 15))
    born_6to12m = point_data.isel(time=slice(15, 21))

    out_vars = [
        lat,
        lon,
    ]
    # Compute mean values for SPI
    inutero_q1_mean = inutero_q1.mean()
    inutero_q2_mean = inutero_q2.mean()
    inutero_q3_mean = inutero_q3.mean()
    born_1m_mean = born_1m.mean()
    born_2to3m_mean = born_2to3m.mean()
    born_3to6m_mean = born_3to6m.mean()
    born_6to12m_mean = born_6to12m.mean()

    return out_vars


In [ ]:
xr.open_dataset(r"Z:\Downloads\wbgt_daily_mean_2000_2021\wbgtmean_2000_daily_ERA5.nc")

In [ ]:
%%timeit -n 1000
ds.sel(lat=0, lon=-50).isel(time=20).mean()

In [ ]:
%%timeit
selection = ds.sel(lat=0, lon=-50).isel(time=20)
for spi in ["spi1", "spi3", "spi6", "spi9", "spi12", "t2m"]:
    value = selection[spi].mean().item()

In [ ]:
from metpy.calc import wet_bulb_temperature
from metpy.units import units
# wet_bulb_temperature(993 * units.hPa, 32 * units.degC, 15 * units.degC)
test = precipitation.isel(time=0, longitude=slice(0, 10), latitude=slice(0, 10))
wet_bulb_temperature(test.sp * units.Pa, test.t2m * units.degK, test.d2m * units.degK)

## Function to assign climate shocks from a date and a point

In [ ]:
climate_data = xr.open_dataset(rf"{DATA_OUT}/Climate_shocks_v2_previous_months.nc")
dates = climate_data.time.values

In [ ]:
def get_climate_shock(from_date, to_date, lat, lon):
    if pd.isna(from_date):
        return np.nan
    
    # Filter point    
    point_data = climate_data.sel(time=slice(from_date, to_date)).sel(lat=lat, lon=lon, method='nearest')
    
    # Get position of original data
    lat = point_data.lat.item()
    lon = point_data.lon.item()

    # Filter by time
    inutero_q1   = point_data.isel(time=slice(0,3))
    inutero_q2   = point_data.isel(time=slice(3,6))
    inutero_q3   = point_data.isel(time=slice(6,9))
    born_1m      = point_data.isel(time=slice(9,10))
    born_2to3m  = point_data.isel(time=slice(10,12))
    born_3to6m  = point_data.isel(time=slice(12,15))
    born_6to12m  = point_data.isel(time=slice(15,21))

    out_vars = [lat, lon, ]
    for prec in ["standarized_precipitation", "standarized_precipitation_3", "standarized_precipitation_6", "standarized_precipitation_12"]:
        # Compute min and max values for both variables
        inutero_q1_mean   = inutero_q1[prec].mean().item()
        inutero_q2_mean   = inutero_q2[prec].mean().item()
        inutero_q3_mean   = inutero_q3[prec].mean().item()
        born_1m_mean      = born_1m[prec].mean().item()
        born_2to3m_mean  = born_2to3m[prec].mean().item()
        born_3to6m_mean  = born_3to6m[prec].mean().item()
        born_6to12m_mean  = born_6to12m[prec].mean().item()

        out_vars_this_prec = [inutero_q1_mean, inutero_q2_mean, inutero_q3_mean, born_1m_mean, born_2to3m_mean, born_3to6m_mean, born_6to12m_mean]
        out_vars += out_vars_this_prec

    return out_vars    


In [ ]:
def get_climate_shock_old(from_date, to_date, lat, lon):
    if pd.isna(from_date):
        return np.nan
    
    # Filter point    
    point_data = climate_data.sel(time=slice(from_date, to_date)).sel(lat=lat, lon=lon, method='nearest')
    
    # Get max and min values for standarized precipitation
    max_prec = point_data["standarized_precipitation"].max().item()
    min_prec = point_data["standarized_precipitation"].min().item()
    max_prec_m = point_data["standarized_precipitation_m"].max().item()
    min_prec_m = point_data["standarized_precipitation_m"].min().item()
    
    # Get position of original data
    lat = point_data.lat.item()
    lon = point_data.lon.item()
    
    return lat, lon, max_prec, min_prec, max_prec_m, min_prec_m

In [ ]:
climate_data.isel(time=slice(100, 110), lat=-50, lon=120)["standarized_precipitation"].mean().item()

In [ ]:
%load_ext line_profiler
def get_climate_shock_prof():
    date = np.random.choice(dates[12:-12])
    from_date, to_date = date + pd.DateOffset(months=-9), date + pd.DateOffset(years=1)
    lat, lon = np.random.uniform(-90, 90), np.random.uniform(-180, 180)
    
    get_climate_shock(from_date, to_date, lat, lon)    
    return

In [ ]:
%lprun -f get_climate_shock_prof get_climate_shock_prof()

In [ ]:
%timeit get_climate_shock_prof()

## Open DHS data and add the shock data to the dataframe

In [ ]:
df = pd.read_stata(rf"{DATA_IN}/DHS/DHSBirthsGlobalAnalysis_04172024.dta")
df['ID'] = df.index

### Create dates variables:
We considered a 

In [ ]:
# Create datetime object from year and month
df["day"] = 1
df["month"] = df["chb_month"].astype(float)
df["year"] = df["chb_year"].astype(float)
df["birthdate"] = pd.to_datetime(df[["year", "month","day"]]).to_numpy()

# Maximum range of dates
df["from_date"] = df["birthdate"] + pd.DateOffset(months=-9) # From in utero (9 months before birth) 
df["to_date"] = df["birthdate"] + pd.DateOffset(years=1) # To the first year of life

# Filter children from_date greater than 1990 (we only have climate data from 1990)
df = df[df["from_date"] > "1990-01-01"]

# # Construct deathdate variable
# df["deathdate"] = df[df["child_agedeath"]<=12].progress_apply(lambda x: x["birthdate"] + pd.DateOffset(months=x["child_agedeath"]), axis=1)

# # Replace to_date with deathdate if the child died
# df["to_date"] = np.where((df["child_agedeath"]<=12) & (df["deathdate"]<df["to_date"]), df["deathdate"], df["to_date"])

# Filter children to_date smalle than 2021 (we only have climate data to 2020)
df = df[df["to_date"] < "2021-01-01"]

In [ ]:
coords_cols = ["lat_climate", "lon_climate"]
prec_cols = ["prec_inutero_q1", "prec_inutero_q2", "prec_inutero_q3", "prec_born_1m", "prec_born_2to3m", "prec_born_3to6m", "prec_born_6to12m"]
prec_3_cols = ["prec_3_inutero_q1", "prec_3_inutero_q2", "prec_3_inutero_q3", "prec_3_born_1m", "prec_3_born_2to3m", "prec_3_born_3to6m", "prec_3_born_6to12m"]
prec_6_cols = ["prec_6_inutero_q1", "prec_6_inutero_q2", "prec_6_inutero_q3", "prec_6_born_1m", "prec_6_born_2to3m", "prec_6_born_3to6m", "prec_6_born_6to12m"]
prec_12_cols = ["prec_12_inutero_q1", "prec_12_inutero_q2", "prec_12_inutero_q3", "prec_12_born_1m", "prec_12_born_2to3m", "prec_12_born_3to6m", "prec_12_born_6to12m"]
all_cols = coords_cols + prec_cols + prec_3_cols + prec_6_cols + prec_12_cols

for n in tqdm(range(0, df.ID.max(), 10_000)):
    if os.path.exists(rf"{DATA_PROC}/births_climate_{n}.csv"):
        print(f"births_climate_{n}.csv exists, moving to next iteration")
        continue
    chunk = df.loc[(df.ID >= n) & (df.ID < n+10_000), ['ID', 'from_date', 'to_date', 'LATNUM', 'LONGNUM']].copy()
    if chunk.shape[0]==0:
        continue
    climate_results = chunk[['from_date', 'to_date', 'LATNUM', 'LONGNUM']].apply(lambda s: get_climate_shock(s['from_date'], s['to_date'], s['LATNUM'], s['LONGNUM']), axis=1)
    climate_results = climate_results.apply(pd.Series)
    climate_results.columns = all_cols
    climate_results["ID"] = chunk["ID"]
    climate_results.to_csv(rf"{DATA_PROC}/births_climate_{n}.csv")
    
# df[all_cols] = climate_data

In [ ]:
# # For debugging
# chunk[['from_date', 'to_date', 'LATNUM', 'LONGNUM']].progress_apply(lambda s: get_climate_shock(s['from_date'], s['to_date'], s['LATNUM'], s['LONGNUM']), axis=1)

In [ ]:
files = os.listdir(rf"{DATA_PROC}") 
files = [f for f in files if f.startswith("births_climate_")]
data = []
for file in tqdm(files):
    df = pd.read_csv(rf"{DATA_PROC}/{file}")
    data += [df]
df = pd.concat(data)

In [ ]:
df = df.drop(columns="Unnamed: 0")
df.to_stata(rf"{DATA_PROC}\ClimateShocks_assigned.dta")

# Example Plots

In [ ]:
import matplotlib.pyplot as plt
pos = np.random.randint(0, 500000)
pos = 428380      
filtered2 = climate_data.standarized_precipitation.sel(lat=df.at[pos, "LATNUM"], lon=df.at[pos, "LONGNUM"], method="nearest")
filtered2.plot(figsize=(12, 2))

plt.axhline(2, color="red")
plt.axhline(-2, color="red")



In [ ]:
climate

In [ ]:
import gc
import pandas as pd
import warnings

warnings.simplefilter(action='ignore', category=pd.errors.PerformanceWarning)

climate = pd.read_stata(rf"{DATA_PROC}\ClimateShocks_assigned.dta")

dhs = pd.read_stata(rf"{DATA_IN}/DHS/DHSBirthsGlobalAnalysis_04172024.dta")
dhs["ID"] = dhs.index

merged = dhs.merge(climate, on="ID")
dhs = 0
climate = 0


In [ ]:
# merged = merged.head(10_000)
merged["lon_climate_2"] = merged["lon_climate"].round(0) 
merged["lon_climate_3"] = merged["lon_climate_2"] - merged["lon_climate_2"].astype(int) % 2 
merged["lat_climate_2"] = merged["lat_climate"].round(0)
merged["lat_climate_3"] = merged["lat_climate_2"] - merged["lat_climate_2"].astype(int) % 2 

merged["ID_cell3"] = merged["lon_climate_3"].astype(str) + "_" + merged["lat_climate_3"].astype(str)
one_hot = pd.get_dummies(merged["ID_cell3"], prefix='ID_cell3')
years_interaction = one_hot.multiply(merged["chb_year"], axis="index")
years_interaction.columns = [f"years_{col}" for col in years_interaction.columns]
months_interaction = one_hot.multiply(merged["chb_year"], axis="index")
months_interaction.columns = [f"months_{col}" for col in months_interaction.columns]
gc.collect()

merged[one_hot.columns] = one_hot
merged[years_interaction.columns] = years_interaction
merged[months_interaction.columns] = months_interaction
gc.collect()

In [ ]:
merged[one_hot.columns] = one_hot
merged[years_interaction.columns] = years_interaction
merged[months_interaction.columns] = months_interaction

In [ ]:
pd.concat([merged, one_hot])

In [ ]:
one_hot.memory_usage().sum() * 1e-9

In [ ]:
import pandas as pd
df = pd.read_stata(rf"{DATA_OUT}\DHSBirthsGlobal&ClimateShocks.dta")

In [ ]:
!py -m pip install fastparquet

In [ ]:
df.to_csv(rf"{DATA_OUT}\DHSBirthsGlobal&ClimateShocks.csv")

In [ ]:
import pandas as pd
pd.read_excel(r"Z:\Downloads\serie2016.xls")

In [92]:
import pandas as pd
import geopandas as gpd

df = pd.read_parquet(r"G:\Maestría\Tesis\Repo\data\data_out\gridded_predictions\mobnet_v3_large_size128_tiles1_sample1\mobnet_v3_large_size128_tiles1_sample1_496_predictions.parquet")
test = gpd.read_feather(r"G:\Maestría\Tesis\Repo\data\data_out\test_datasets\mobnet_v3_large_size128_tiles1_sample1_aug_test_dataframe.feather")

In [93]:
df = df.merge(test, on="link")
df = df[df.prediction!=0.45116878] # Remove black predictions

In [94]:
import seaborn as sns
data = df.groupby("link")[["real_value", "prediction"]].mean()

data = data.reset_index()

In [102]:
def plot_predictions_vs_real(
    best_case,
):
    import plotly.express as px
    from plotly import graph_objects as go

    axis_range = [-2.2, 2.2]

    import seaborn as sns

    fig = px.scatter(
        best_case, x="real_value", y="prediction", hover_data=["link"]
    )
    
    fig.update_yaxes(range=axis_range, title="Predicción Media del Radio Censal (estandarizada)", title_font=dict(size=18)) 
    fig.update_xaxes(range=axis_range, title="Ingreso Medio del Radio Censal (estandarizado)",title_font=dict(size=18))
    fig.update_layout(
        autosize=False,
        width=800,
        height=700,
    )

    # Add 45° line
    line_fig = go.Figure(
        data=go.Scatter(
            x=best_case["real_value"],
            y=best_case["real_value"],
            mode="lines",
            name="45°",
        )
    )
    fig.add_trace(line_fig.data[0])
    fig.update_traces(marker=dict(size=5))
    # Reduce margin
    fig.update_layout(margin=dict(l=2, r=2, b=2, t=2))

    return fig

fig = plot_predictions_vs_real(
    data,
)

# Exoport as png
fig.write_image(r"G:\Maestría\Tesis\Repo\outputs\mobnet_v3_large_size128_tiles1_sample1_aug\mobnet_v3_large_size128_tiles1_sample1_aug.png", scale=4)

In [104]:
fig.show()

In [97]:
data["error"] = data["real_value"] - data["prediction"]
ss_res = (data["error"] ** 2).sum()  # Sum of squared residuals
ss_tot = ((data["real_value"] - data["real_value"].mean()) ** 2).sum()  # Total sum of squares
r2 = 1 - ss_res / ss_tot
r2


0.769771158695221

In [31]:
df2 = pd.read_parquet(r"G:\Maestría\Tesis\Repo\data\data_out\gridded_predictions\effnet_v2S_lr0.0001_size128_y2013-2018-2022_stack1-4\effnet_v2S_lr0.0001_size128_y2013-2018-2022_stack1-4_141_predictions_2013.parquet")

In [44]:
import seaborn as sns
data2 = df2.groupby("link")[["real_value", "prediction"]].mean()

data2 = data2.reset_index()

In [67]:
plot_predictions_vs_real(
    data2,
)